#**IFCE - Programa Institucional de Bolsas de Iniciação Científica – PIBIC**

**Título:** Avaliação de Desempenho de Classificadores a Partir de DadosRelacionados a Precipitação Pluviométrica Coletados por EstaçãoMeteorológica Automática

**Discente:** Ananias Caetano de Oliveira

**Orientador:** Rhyan Ximenes de Brito

**Coorientador:** Adonias Caetano de Oliveira

**Curso:** Bacharelado em Ciência da Computação

In [ ]:
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [ ]:
!pip install plotly --upgrade

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install -q "tqdm>=4.36.1"

In [1]:
!pip install colorama

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


#**Etapa 1: Leitura do dataset TIANGUA(A368) de Precipitações**

**Descrição do dataset:** O dataset possui 27695 registros e 19 atributos, dos quais o último atributo "Chuva (mm)" determina a quantidade em milímetros de chuva para um período.

**Atributos:**

* **Data:** Data de registro;
* **Hora (UTC):** Hora de registro;
* **Temp. Ins. (C):** Temperatura Instantânea do Ar;
* **Temp. Max. (C):** Temperatura Máxima do Ar;
* **Temp. Min. (C):** Temperatura Mínima do Ar;
* **Umi. Ins. (%):** Umidade Relativa Instantânea do Ar;
* **Umi. Max. (%):** Umidade Relativa Máxima do Ar;
* **Umi. Min. (%):** Umidade Relativa Mínima do Ar;
* **Pto Orvalho Ins. (C):** Temperatura Instantânea do Ponto de Orvalho;
* **Pto Orvalho Max. (C):** Temperatura Máxima do Ponto de Orvalho;
* **Pto Orvalho Min. (C):** Temperatura Mínima do Ponto de Orvalho;
* **Pressao Ins. (hPa):** Pressão Atmosférica Instantânea do Ar;
* **Pressao Max. (hPa):** Pressão Atmosférica Máxima do Ar;
* **Pressao Min. (hPa):** Pressão Atmosférica Mínima do Ar;
* **Vel. Vento (m/s):** Velocidade Instantânea do Vento;
* **Dir. Vento (m/s):** Direção do Vento;
* **Raj. Vento (m/s):** Intensidade da Rajada do Vento;
* **Radiacao (KJ/m²):** Radiação Solar;
* **Chuva (mm):** Precipitação acumulada no período;

In [ ]:
# Importando biblioteca pandas
import pandas as pd
import numpy as np
# PLOTS
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
import matplotlib.pyplot as plt
from plotly import figure_factory as ff
from tqdm import tqdm
from colorama import Fore
# PRÉ PROCESSO
from imblearn.under_sampling import RandomUnderSampler
from scipy import stats
# METODOS DE CLASSIFICAÇÃO
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
#----------------------------------------------------------------------
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score, precision_score, recall_score, f1_score
import warnings

**(2) Adicionando a base de dados de Tianguá da Estação Meteorológica do INMET**

In [ ]:
base = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/ENUCOMPI 2021 ANANIAS/dataset/tiangua(A368).csv', encoding = 'UTF-8', sep=';', decimal=",")

In [ ]:
base

Data  Hora (UTC)  Temp. Ins. (C)  Temp. Max. (C)  Temp. Min. (C)  \
0      15/03/2018         100             NaN             NaN             NaN   
1      15/03/2018         200             NaN             NaN             NaN   
2      15/03/2018         300             NaN             NaN             NaN   
3      15/03/2018         400             NaN             NaN             NaN   
4      15/03/2018         500             NaN             NaN             NaN   
...           ...         ...             ...             ...             ...   
27690  11/05/2021        1900             NaN             NaN             NaN   
27691  11/05/2021        2000             NaN             NaN             NaN   
27692  11/05/2021        2100             NaN             NaN             NaN   
27693  11/05/2021        2200             NaN             NaN             NaN   
27694  11/05/2021        2300             NaN             NaN             NaN   

       Umi. Ins. (%)  Umi. Max. (%)  Umi. Min. (%)  Pto Orvalho Ins. (C)  \
0                NaN            NaN            NaN                   NaN   
1                NaN            NaN            NaN                   NaN   
2                NaN            NaN            NaN                   NaN   
3                NaN            NaN            NaN                   NaN   
4                NaN            NaN            NaN                   NaN   
...              ...            ...            ...                   ...   
27690            NaN            NaN            NaN                   NaN   
27691            NaN            NaN            NaN                   NaN   
27692            NaN            NaN            NaN                   NaN   
27693            NaN            NaN            NaN                   NaN   
27694            NaN            NaN            NaN                   NaN   

       Pto Orvalho Max. (C)  Pto Orvalho Min. (C)  Pressao Ins. (hPa)  \
0                       NaN                   NaN                 NaN   
1                       NaN                   NaN                 NaN   
2                       NaN                   NaN                 NaN   
3                       NaN                   NaN                 NaN   
4                       NaN                   NaN                 NaN   
...                     ...                   ...                 ...   
27690                   NaN                   NaN                 NaN   
27691                   NaN                   NaN                 NaN   
27692                   NaN                   NaN                 NaN   
27693                   NaN                   NaN                 NaN   
27694                   NaN                   NaN                 NaN   

       Pressao Max. (hPa)  Pressao Min. (hPa)  Vel. Vento (m/s)  \
0                     NaN                 NaN               NaN   
1                     NaN                 NaN               NaN   
2                     NaN                 NaN               NaN   
3                     NaN                 NaN               NaN   
4                     NaN                 NaN               NaN   
...                   ...                 ...               ...   
27690                 NaN                 NaN               NaN   
27691                 NaN                 NaN               NaN   
27692                 NaN                 NaN               NaN   
27693                 NaN                 NaN               NaN   
27694                 NaN                 NaN               NaN   

       Dir. Vento (m/s)  Raj. Vento (m/s)  Radiacao (KJ/m²)  Chuva (mm)  \
0                   NaN               NaN               NaN         NaN   
1                   NaN               NaN               NaN         NaN   
2                   NaN               NaN               NaN         NaN   
3                   NaN               NaN               NaN         NaN   
4                   NaN               NaN               NaN         Na

**Descrição da base de dados**

In [ ]:
base.describe()

Hora (UTC)  Temp. Ins. (C)  Temp. Max. (C)  Temp. Min. (C)  \
count  27695.000000    27655.000000    27655.000000    27655.000000   
mean    1150.041524       23.051069       23.637107       22.498684   
std      692.209156        3.080640        3.277051        2.872251   
min        0.000000       13.500000       14.200000       13.200000   
25%      600.000000       20.800000       21.100000       20.600000   
50%     1200.000000       22.100000       22.600000       21.700000   
75%     1750.000000       25.200000       26.100000       24.300000   
max     2300.000000       32.900000       33.300000       32.000000   

       Umi. Ins. (%)  Umi. Max. (%)  Umi. Min. (%)  Pto Orvalho Ins. (C)  \
count   27476.000000    27484.00000   27484.000000          27476.000000   
mean       78.930667       81.54650      76.148013             18.736272   
std        15.681350       14.69262      16.512566              1.869267   
min        27.000000       28.00000      24.000000              9.200000   
25%        70.000000       74.00000      66.000000             17.700000   
50%        84.000000       87.00000      81.000000             19.100000   
75%        92.000000       93.00000      90.000000             20.100000   
max        98.000000       99.00000      98.000000             23.200000   

       Pto Orvalho Max. (C)  Pto Orvalho Min. (C)  Pressao Ins. (hPa)  \
count          27452.000000          27452.000000        27655.000000   
mean              19.188325             18.310068          928.687113   
std                1.810328              1.936144            1.711051   
min               10.000000              8.100000          922.100000   
25%               18.100000             17.200000          927.500000   
50%               19.400000             18.700000          928.700000   
75%               20.500000             19.800000          929.900000   
max               23.900000             22.500000          934.300000   

       Pressao Max. (hPa)  Pressao Min. (hPa)  Vel. Vento (m/s)  \
count        27655.000000        27655.000000      23916.000000   
mean           928.935777          928.436728          3.464438   
std              1.691039            1.711619          1.741211   
min            922.300000          921.900000          0.100000   
25%            927.800000          927.200000          2.200000   
50%            928.900000          928.400000          3.400000   
75%            930.100000          929.600000          4.600000   
max            934.400000          934.200000         11.100000   

       Dir. Vento (m/s)  Raj. Vento (m/s)  Radiacao (KJ/m²)    Chuva (mm)  \
count      23916.000000      23917.000000      15006.000000  27655.000000   
mean          92.709107          7.208647       1568.715945      0.137559   
std           47.041549          2.933466       1174.382462      1.243152   
min            1.000000          0.500000          0.000000      0.000000   
25%           64.000000          5.100000        413.455000      0.000000   
50%           92.000000          7.100000       1515.530000      0.000000   
75%          109.000000          9.000000       2580.107500      0.000000   
max          360.000000         20.500000       4238.680000     41.200000   

       Unnamed: 19  
count          0.0  
mean           NaN  
std            NaN  
min            NaN  
25%            NaN  
50%            NaN  
75%            NaN  
max            NaN

**Número de registros 'NaN' para cada atributo**

In [ ]:
base.isnull().sum()

Data                        0
Hora (UTC)                  0
Temp. Ins. (C)             40
Temp. Max. (C)             40
Temp. Min. (C)             40
Umi. Ins. (%)             219
Umi. Max. (%)             211
Umi. Min. (%)             211
Pto Orvalho Ins. (C)      219
Pto Orvalho Max. (C)      243
Pto Orvalho Min. (C)      243
Pressao Ins. (hPa)         40
Pressao Max. (hPa)         40
Pressao Min. (hPa)         40
Vel. Vento (m/s)         3779
Dir. Vento (m/s)         3779
Raj. Vento (m/s)         3778
Radiacao (KJ/m²)        12689
Chuva (mm)                 40
Unnamed: 19             27695
dtype: int64

**Gerando uma cópia da base de dados que irá sofrer o Pré-Processamento**

In [ ]:
dataset = base.copy()

#**Etapa 2: Pré-processamento de dados**

**(1) Remoção dos registros com atributo "Chuva (mm)" vazios**

In [ ]:
# removendo colunas que não serão usadas
# apagar somente os registros sem resultados
dataset.dropna(subset=['Chuva (mm)'], inplace=True)
dataset.dropna(subset=['Umi. Ins. (%)'], inplace=True)
dataset.dropna(subset=['Umi. Max. (%)'], inplace=True)
dataset.dropna(subset=['Pto Orvalho Max. (C)'], inplace=True)
dataset.dropna(subset=['Vel. Vento (m/s)'], inplace=True)
dataset = dataset.drop(columns=['Radiacao (KJ/m²)'])
dataset = dataset.drop(columns=['Unnamed: 19'])

In [ ]:
dataset

Data  Hora (UTC)  Temp. Ins. (C)  Temp. Max. (C)  Temp. Min. (C)  \
19     15/03/2018        2000            25.5            26.5            25.5   
20     15/03/2018        2100            23.3            25.5            23.3   
21     15/03/2018        2200            22.8            23.3            22.7   
22     15/03/2018        2300            22.5            23.0            22.5   
23     16/03/2018           0            22.1            22.6            22.0   
...           ...         ...             ...             ...             ...   
27669  10/05/2021        2200            22.1            22.9            22.1   
27670  10/05/2021        2300            21.3            22.1            21.3   
27671  11/05/2021           0            21.7            21.7            21.2   
27672  11/05/2021         100            22.0            22.0            21.4   
27673  11/05/2021         200            21.9            22.0            21.8   

       Umi. Ins. (%)  Umi. Max. (%)  Umi. Min. (%)  Pto Orvalho Ins. (C)  \
19              75.0           76.0           64.0                  20.8   
20              83.0           85.0           75.0                  20.3   
21              89.0           90.0           83.0                  21.0   
22              91.0           91.0           87.0                  20.9   
23              90.0           93.0           90.0                  20.4   
...              ...            ...            ...                   ...   
27669           90.0           90.0           84.0                  20.3   
27670           93.0           93.0           90.0                  20.0   
27671           92.0           93.0           92.0                  20.2   
27672           89.0           92.0           89.0                  20.1   
27673           88.0           90.0           88.0                  19.7   

       Pto Orvalho Max. (C)  Pto Orvalho Min. (C)  Pressao Ins. (hPa)  \
19                     21.4                  19.1               926.8   
20                     21.3                  20.3               927.4   
21                     21.0                  20.4               927.9   
22                     21.0                  20.7               928.7   
23                     21.1                  20.4               929.3   
...                     ...                   ...                 ...   
27669                  20.3                  20.0               928.8   
27670                  20.3                  20.0               929.4   
27671                  20.2                  20.0               930.0   
27672                  20.2                  20.1               930.1   
27673                  20.1                  19.7               929.9   

       Pressao Max. (hPa)  Pressao Min. (hPa)  Vel. Vento (m/s)  \
19                  926.8               926.5               3.1   
20                  927.4               926.8               2.8   
21                  927.9               927.4               3.2   
22                  928.7               927.9               3.1   
23                  929.3               928.5               4.0   
...                   ...                 ...               ...   
27669               928.8               928.2               2.4   
27670               929.4               928.8               1.9   
27671               930.0               929.4               1.1   
27672               930.1               930.0               2.1   
27673               930.2               929.9               2.7   

       Dir. Vento (m/s)  Raj. Vento (m/s)  Chuva (mm)  
19                 67.0               7.3         0.0  
20                 41.0               5.9         0.0  
21                 55.0               6.0         0.0  
22                 45.0               8.6         0.0  
23                 45.0               9.2         0.0  
...                 ...               ...         ...  
27669             119.0               4.7         0.0

**Número de registros 'NaN' para cada atributo**

In [ ]:
dataset.isnull().sum()

Data                    0
Hora (UTC)              0
Temp. Ins. (C)          0
Temp. Max. (C)          0
Temp. Min. (C)          0
Umi. Ins. (%)           0
Umi. Max. (%)           0
Umi. Min. (%)           0
Pto Orvalho Ins. (C)    0
Pto Orvalho Max. (C)    0
Pto Orvalho Min. (C)    0
Pressao Ins. (hPa)      0
Pressao Max. (hPa)      0
Pressao Min. (hPa)      0
Vel. Vento (m/s)        0
Dir. Vento (m/s)        0
Raj. Vento (m/s)        0
Chuva (mm)              0
dtype: int64

**(2) Substituindo a Data por o número de dias do ano**

É substituido a data por o número de dias do ano para a data respectiva, assim apenas guardando o periodo do ano.

In [ ]:
Data_tempo = dataset.iloc[:, 0:1]
dias_mes = np.array([31, 28, 31, 30, 31, 30, 31, 31, 30, 31, 30, 31])
dias_ano = np.array([365, 365, 366, 365]) # 2018 a 2021

for i in dataset.index:
  date = dataset.loc[i, 'Data']
  array_data = date.split('/')
  hora = int(dataset.loc[i, 'Hora (UTC)'])

  dia = int(array_data[0])
  mes = int(array_data[1])
  ano = int(array_data[2])
  hora = int(hora/100)
  
  # Calcula a quantidade de dias do ano não bissexto
  dias_somados = dia + dias_mes[0:mes-1].sum() + dias_ano[0:(ano-2018)].sum()

  # Se o ano for bissexto adiciona 1 dia. 
  if mes > 2 and (ano%4==0 and ano%100!=0 or ano%400==0):
    dias_somados += 1
  dataset.loc[i, 'Data'] = str(ano)+'-'+str(mes)+'-'+str(dia)+' '+str(hora)+':00:00'
  Data_tempo.loc[i, 'Data'] = dias_somados

**Tornando Data como datetime**

In [ ]:
dataset['Data'] = pd.to_datetime(dataset['Data'])

**Tornando Data como index da base**

In [ ]:
dataset = dataset.set_index('Data')
dataset = dataset.drop(columns=['Hora (UTC)'])

**(3) Tornando a ultima coluna como 0 e 1**

In [ ]:
dataset.loc[dataset['Chuva (mm)'] > 0, 'Chuva (mm)'] = 1  # atualizando o campo para a média
dataset["Chuva (mm)"] = dataset["Chuva (mm)"].astype(int)

In [ ]:
dataset

Temp. Ins. (C)  Temp. Max. (C)  Temp. Min. (C)  \
Data                                                                  
2018-03-15 20:00:00            25.5            26.5            25.5   
2018-03-15 21:00:00            23.3            25.5            23.3   
2018-03-15 22:00:00            22.8            23.3            22.7   
2018-03-15 23:00:00            22.5            23.0            22.5   
2018-03-16 00:00:00            22.1            22.6            22.0   
...                             ...             ...             ...   
2021-05-10 22:00:00            22.1            22.9            22.1   
2021-05-10 23:00:00            21.3            22.1            21.3   
2021-05-11 00:00:00            21.7            21.7            21.2   
2021-05-11 01:00:00            22.0            22.0            21.4   
2021-05-11 02:00:00            21.9            22.0            21.8   

                     Umi. Ins. (%)  Umi. Max. (%)  Umi. Min. (%)  \
Data                                                               
2018-03-15 20:00:00           75.0           76.0           64.0   
2018-03-15 21:00:00           83.0           85.0           75.0   
2018-03-15 22:00:00           89.0           90.0           83.0   
2018-03-15 23:00:00           91.0           91.0           87.0   
2018-03-16 00:00:00           90.0           93.0           90.0   
...                            ...            ...            ...   
2021-05-10 22:00:00           90.0           90.0           84.0   
2021-05-10 23:00:00           93.0           93.0           90.0   
2021-05-11 00:00:00           92.0           93.0           92.0   
2021-05-11 01:00:00           89.0           92.0           89.0   
2021-05-11 02:00:00           88.0           90.0           88.0   

                     Pto Orvalho Ins. (C)  Pto Orvalho Max. (C)  \
Data                                                              
2018-03-15 20:00:00                  20.8                  21.4   
2018-03-15 21:00:00                  20.3                  21.3   
2018-03-15 22:00:00                  21.0                  21.0   
2018-03-15 23:00:00                  20.9                  21.0   
2018-03-16 00:00:00                  20.4                  21.1   
...                                   ...                   ...   
2021-05-10 22:00:00                  20.3                  20.3   
2021-05-10 23:00:00                  20.0                  20.3   
2021-05-11 00:00:00                  20.2                  20.2   
2021-05-11 01:00:00                  20.1                  20.2   
2021-05-11 02:00:00                  19.7                  20.1   

                     Pto Orvalho Min. (C)  Pressao Ins. (hPa)  \
Data                                                            
2018-03-15 20:00:00                  19.1               926.8   
2018-03-15 21:00:00                  20.3               927.4   
2018-03-15 22:00:00                  20.4               927.9   
2018-03-15 23:00:00                  20.7               928.7   
2018-03-16 00:00:00                  20.4               929.3   
...                                   ...                 ...   
2021-05-10 22:00:00                  20.0               928.8   
2021-05-10 23:00:00                  20.0               929.4   
2021-05-11 00:00:00                  20.0               930.0   
2021-05-11 01:00:00                  20.1               930.1   
2021-05-11 02:00:00                  19.7               929.9   

                     Pressao Max. (hPa)  Pressao Min. (hPa)  Vel. Vento (m/s)  \
Data                                                                            
2018-03-15 20:00:00               926.8               926.5               3.1   
2018-03-15 21:00:00               927.4               926.8               2.8   
2018-03-15 22:00:00               927.9               927.4               3.2   
2018-03-15 23:00:00               928.7               927.9               3.1   
2018-03-

**(4) Separando a base de dados em conjunto de atributos e atributo alvo**

In [ ]:
Data = dataset.index # Registro de Dia e Hora - Dia 74 (15/03/2018) a Dia 1227 (11/05/2021)
X = dataset.iloc[:, 0:15].values # X
y = dataset.iloc[:, 15].values # Y

In [ ]:
print('X:\n', X)
print('y:\n', y)
print('\nX Shape: ', X.shape)
print('\ny Shape: ', y.shape)

X:
 [[ 25.5  26.5  25.5 ...   3.1  67.    7.3]
 [ 23.3  25.5  23.3 ...   2.8  41.    5.9]
 [ 22.8  23.3  22.7 ...   3.2  55.    6. ]
 ...
 [ 21.7  21.7  21.2 ...   1.1 132.    3. ]
 [ 22.   22.   21.4 ...   2.1 110.    3.3]
 [ 21.9  22.   21.8 ...   2.7 115.    4.8]]
y:
 [0 0 0 ... 0 0 0]

X Shape:  (23670, 15)

y Shape:  (23670,)


**(5) Aplicando UnderSampler para Balancear as classes**

In [ ]:
undersample = RandomUnderSampler()
X_processed, y = undersample.fit_resample(X, y)

In [ ]:
print('X_process:\n', X_processed)
print('y_process:\n', y)
print('\nX_process Shape: ', X_processed.shape)
print('\ny_process Shape: ', y.shape)

X_process:
 [[25.2 25.3 23.5 ...  4.8 93.   9.2]
 [22.5 23.4 22.4 ...  0.9 15.   3.8]
 [20.4 20.8 20.4 ...  2.  88.   4.3]
 ...
 [21.4 21.7 21.4 ...  3.1 81.   6.1]
 [21.5 21.5 21.3 ...  4.5 89.   7.4]
 [21.4 21.6 21.4 ...  4.5 92.   7.9]]
y_process:
 [0 0 0 ... 1 1 1]

X_process Shape:  (2886, 15)

y_process Shape:  (2886,)


**(6) Normalizando os dados usando Z-Score**

In [ ]:
X_scaled = stats.zscore(X_processed)

In [ ]:
print('X__scaled:\n', X_scaled)

X__scaled:
 [[ 1.12615475e+00  7.78054141e-01  6.83647652e-01 ...  9.71268178e-01
   1.31379958e-03  7.11107331e-01]
 [ 3.61597133e-02  9.33515127e-02  1.99679265e-01 ... -1.38807397e+00
  -1.40700428e+00 -1.14573316e+00]
 [-8.11614206e-01 -8.43609978e-01 -6.80263258e-01 ... -7.22618494e-01
  -8.89630003e-02 -9.73803483e-01]
 ...
 [-4.07912340e-01 -5.19277154e-01 -2.40291996e-01 ... -5.71630155e-02
  -2.15350520e-01 -3.54856653e-01]
 [-3.67542153e-01 -5.91351115e-01 -2.84289123e-01 ...  7.89780321e-01
  -7.09076403e-02  9.21605014e-02]
 [-4.07912340e-01 -5.55314135e-01 -2.40291996e-01 ...  7.89780321e-01
  -1.67415604e-02  2.64090176e-01]]


# **Etapa 3: Classificação**

**Implementando ELM para utilização na classificação**

In [ ]:
# Final edited date: 2018.3.7
# Author: Li Xudong, from NSSC.CAS Beijing
# Version: 1.0
# Description: Extreme Learning Machine (ELM) class
# Methods:
#   fit(algorithm)
#   predict(x)
#   score(x, y)
import numpy as np
from scipy.linalg import pinv2, inv
import time

class elm():
    '''
    Function: elm class init
    -------------------
    Parameters:
    shape: list, shape[hidden units, output units]
        numbers of hidden units and output units
    activation_function: str, 'sigmoid', 'relu', 'sin', 'tanh' or 'leaky_relu'
        Activation function of neurals
    x: array, shape[samples, features]
        train data
    y: array, shape[samples, ]
        labels
    C: float
        regularization parameter
    elm_type: str, 'clf' or 'reg'
        'clf' means ELM solve classification problems, 'reg' means ELM solve regression problems.
    one_hot: bool, Ture or False, default True 
        The parameter is useful only when elm_type == 'clf'. If the labels need to transformed to
        one_hot, this parameter is set to be True
    random_type: str, 'uniform' or 'normal', default:'normal'
        Weight initialization method
    '''
    def __init__(self, hidden_units, activation_function,  x, y, C, elm_type, one_hot=True, random_type='normal'):
        self.hidden_units = hidden_units
        self.activation_function = activation_function
        self.random_type = random_type
        self.x = x
        self.y = y
        self.C = C
        self.class_num = np.unique(self.y).shape[0]     
        self.beta = np.zeros((self.hidden_units, self.class_num))   
        self.elm_type = elm_type
        self.one_hot = one_hot

        # if classification problem and one_hot == True
        if elm_type == 'clf' and self.one_hot:
            self.one_hot_label = np.zeros((self.y.shape[0], self.class_num))
            for i in range(self.y.shape[0]):
                self.one_hot_label[i, int(self.y[i])] = 1

        # Randomly generate the weight matrix and bias vector from input to hidden layer
        # 'uniform': uniform distribution
        # 'normal': normal distribution
        if self.random_type == 'uniform':
            self.W = np.random.uniform(low=0, high=1, size=(self.hidden_units, self.x.shape[1]))
            self.b = np.random.uniform(low=0, high=1, size=(self.hidden_units, 1))
        if self.random_type == 'normal':
            self.W = np.random.normal(loc=0, scale=0.5, size=(self.hidden_units, self.x.shape[1]))
            self.b = np.random.normal(loc=0, scale=0.5, size=(self.hidden_units, 1))


    def setXandY():
        self.x = x
        self.y = y

    # compute the output of hidden layer according to different activation function
    def __input2hidden(self, x):
        self.temH = np.dot(self.W, x.T) + self.b

        if self.activation_function == 'sigmoid':
            self.H = 1/(1 + np.exp(- self.temH))

        if self.activation_function == 'relu':
            self.H = self.temH * (self.temH > 0)

        if self.activation_function == 'sin':
            self.H = np.sin(self.temH)

        if self.activation_function == 'tanh':
            self.H = (np.exp(self.temH) - np.exp(-self.temH))/(np.exp(self.temH) + np.exp(-self.temH))

        if self.activation_function == 'leaky_relu':
            self.H = np.maximum(0, self.temH) + 0.1 * np.minimum(0, self.temH)

        return self.H

    # compute the output
    def __hidden2output(self, H):
        self.output = np.dot(H.T, self.beta)
        return self.output

    '''
    Function: Train the model, compute beta matrix, the weight matrix from hidden layer to output layer
    ------------------
    Parameter:
    algorithm: str, 'no_re', 'solution1' or 'solution2'
        The algorithm to compute beta matrix
    ------------------
    Return:
    beta: array
        the weight matrix from hidden layer to output layer
    train_score: float
        the accuracy or RMSE
    train_time: str
        time of computing beta
    '''
    def fit(self, algorithm):
        self.time1 = time.clock()   # compute running time
        self.H = self.__input2hidden(self.x)
        if self.elm_type == 'clf':
            if self.one_hot:
                self.y_temp = self.one_hot_label
            else:
                self.y_temp = self.y
        if self.elm_type == 'reg':
            self.y_temp = self.y
        # no regularization
        if algorithm == 'no_re':
            self.beta = np.dot(pinv2(self.H.T), self.y_temp)
        # faster algorithm 1
        if algorithm == 'solution1':
            self.tmp1 = inv(np.eye(self.H.shape[0])/self.C + np.dot(self.H, self.H.T))
            self.tmp2 = np.dot(self.tmp1, self.H)
            self.beta = np.dot(self.tmp2, self.y_temp)
        # faster algorithm 2
        if algorithm == 'solution2':
            self.tmp1 = inv(np.eye(self.H.shape[0])/self.C + np.dot(self.H, self.H.T))
            self.tmp2 = np.dot(self.H.T, self.tmp1)
            self.beta = np.dot(self.tmp2.T, self.y_temp)
        self.time2 = time.clock()

        # compute the results
        self.result = self.__hidden2output(self.H)
        # If the problem if classification problem, the output is softmax
        if self.elm_type == 'clf':
            self.result = np.exp(self.result)/np.sum(np.exp(self.result), axis=1).reshape(-1, 1)

        # Evaluate training results
        # If problem is classification, compute the accuracy
        # If problem is regression, compute the RMSE
        if self.elm_type == 'clf':
            self.y_ = np.where(self.result == np.max(self.result, axis=1).reshape(-1, 1))[1]
            self.correct = 0
            for i in range(self.y.shape[0]):
                if self.y_[i] == self.y[i]:
                    self.correct += 1
            self.train_score = self.correct/self.y.shape[0]
        if self.elm_type == 'reg':
            self.train_score = np.sqrt(np.sum((self.result - self.y) * (self.result - self.y))/self.y.shape[0])
        train_time = str(self.time2 - self.time1)
        return self.beta, self.train_score, train_time

    '''
    Function: compute the result given data
    ---------------
    Parameters:
    x: array, shape[samples, features]
    ---------------
    Return:
    y_: array
        predicted results
    '''
    def predict(self, x):
        self.H = self.__input2hidden(x)
        self.y_ = self.__hidden2output(self.H)
        if self.elm_type == 'clf':
            self.y_ = np.where(self.y_ == np.max(self.y_, axis=1).reshape(-1, 1))[1]

        return self.y_

    '''
    Function: compute accuracy or RMSE given data and labels
    -------------
    Parameters:
    x: array, shape[samples, features]
    y: array, shape[samples, ]
    -------------
    Return:
    test_score: float, accuracy or RMSE
    '''
    def score(self, x, y):
        self.prediction = self.predict(x)
        if self.elm_type == 'clf':
            self.correct = 0
            for i in range(y.shape[0]):
                if self.prediction[i] == y[i]:
                    self.correct += 1
            self.test_score = self.correct/y.shape[0]
        if self.elm_type == 'reg':
            self.test_score = np.sqrt(np.sum((self.result - self.y) * (self.result - self.y))/self.y.shape[0])

        return self.test_score

**Definindo máximo de rodadas e tamanho da base de teste**

In [ ]:
MAX_RODADAS = 10
TAM_VALIDACAO = 0.2

In [ ]:
def execute_classificacao(model, X, Y):

  # dicionário para armazenar os resultados
  resultados = {
    'ACCURACY': [], # Acurácia
    'PRECISION': [], # Precisão
    'RECALL': [], # Sensibilidade
    'F1': [], # F1-Score
    'TN (%)': [], 
    'FN (%)': [], 
    'FP (%)': [], 
    'TP (%)': [], 
    'TN': [], 
    'FN': [], 
    'FP': [], 
    'TP': []
  }
  precisao = [];
  
  with tqdm(total=MAX_RODADAS, desc='Classificação', bar_format="{l_bar}%s{bar}%s{r_bar}" % (Fore.BLUE, Fore.RESET)  ) as pbar:
    rodada = 0
    while rodada < MAX_RODADAS:

      # Divisão do dataset em subconjunto de treinamento e validação
      X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=TAM_VALIDACAO)

      # Treinamento do modelo de regressão
      model.fit(X_train, y_train)

      # Previsão das saídas do conjunto de treinamento
      y_train_predicted = model.predict(X_train)

      # Validação: Previsão das saídas do conjunto de teste
      y_test_predict = model.predict(X_test)
      
      # Score de precisão
      resultados['ACCURACY'].append(accuracy_score(y_test, y_test_predict, normalize=True)*100)
      resultados['PRECISION'].append(precision_score(y_test, y_test_predict)*100)
      resultados['RECALL'].append(recall_score(y_test, y_test_predict)*100)
      resultados['F1'].append(f1_score(y_test, y_test_predict)*100)
      
      # Matriz de Confusao
      matriz_confusao = confusion_matrix(y_test, y_test_predict, normalize='true')
      
      resultados['TN (%)'].append(matriz_confusao[0][0] * 100)
      resultados['FN (%)'].append(matriz_confusao[0][1] * 100)
      resultados['FP (%)'].append(matriz_confusao[1][0] * 100)
      resultados['TP (%)'].append(matriz_confusao[1][1] * 100)
      
      matriz_confusao = confusion_matrix(y_test, y_test_predict)
      
      resultados['TN'].append(matriz_confusao[0][0])
      resultados['FN'].append(matriz_confusao[0][1])
      resultados['FP'].append(matriz_confusao[1][0])
      resultados['TP'].append(matriz_confusao[1][1])
      
      rodada += 1
      pbar.update(1)
  return resultados

**Função de Execução ELM**

In [ ]:
def execute_classificacaoELM(X, Y, parametro_elm):

  # dicionário para armazenar os resultados
  resultados = {
    'ACCURACY': [], # Acurácia
    'PRECISION': [], # Precisão
    'RECALL': [], # Sensibilidade
    'F1': [], # F1-Score
    'TN (%)': [], 
    'FN (%)': [], 
    'FP (%)': [], 
    'TP (%)': [], 
    'TN': [], 
    'FN': [], 
    'FP': [], 
    'TP': []
  }

  with tqdm(total=MAX_RODADAS, desc='Classificação', bar_format="{l_bar}%s{bar}%s{r_bar}" % (Fore.BLUE, Fore.RESET)  ) as pbar:
    rodada = 0
    while rodada < MAX_RODADAS:

      # Divisão do dataset em subconjunto de treinamento e validação
      X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=TAM_VALIDACAO)

      # CRIANDO O CLASSIFICADOR
      clf = elm(hidden_units = parametro_elm['HIDDEN_UNITS'], activation_function = parametro_elm['ACTIVATION_FUNCTION'], x = X_train, y = y_train, C = parametro_elm['C'], elm_type = 'clf', one_hot=True, random_type=parametro_elm['RANDOM_TYPE'])

      # Treinamento do modelo de regressão
      clf.fit(algorithm ='solution2')

      # Previsão das saídas do conjunto de treinamento
      y_train_predicted = clf.predict(X_train)

      # Validação: Previsão das saídas do conjunto de teste
      y_test_predict = clf.predict(X_test)
      
      # Score de precisão
      resultados['ACCURACY'].append(accuracy_score(y_test, y_test_predict, normalize=True)*100)
      resultados['PRECISION'].append(precision_score(y_test, y_test_predict)*100)
      resultados['RECALL'].append(recall_score(y_test, y_test_predict)*100)
      resultados['F1'].append(f1_score(y_test, y_test_predict)*100)
      
      # Matriz de Confusao
      matriz_confusao = confusion_matrix(y_test, y_test_predict, normalize='true')
      
      resultados['TN (%)'].append(matriz_confusao[0][0] * 100)
      resultados['FN (%)'].append(matriz_confusao[0][1] * 100)
      resultados['FP (%)'].append(matriz_confusao[1][0] * 100)
      resultados['TP (%)'].append(matriz_confusao[1][1] * 100)
      
      matriz_confusao = confusion_matrix(y_test, y_test_predict)
      
      resultados['TN'].append(matriz_confusao[0][0])
      resultados['FN'].append(matriz_confusao[0][1])
      resultados['FP'].append(matriz_confusao[1][0])
      resultados['TP'].append(matriz_confusao[1][1])
      
      rodada += 1
      pbar.update(1)
  return resultados

## **Aplicação do Random Forest Classifier** 

In [ ]:
resultados_rd = []

# Variancia dos Parametros
parametros_rd = {
    1: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    2: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    3: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    4: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    5: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    6: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    7: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    8: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'auto'},
    9: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    10: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    11: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    12: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    13: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    14: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    15: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    16: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'auto'},
    17: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    18: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    19: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    20: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    21: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    22: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    23: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    24: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'sqrt'},
    25: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    26: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    27: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    28: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    29: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    30: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    31: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    32: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'sqrt'},
    33: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    34: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    35: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    36: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    37: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    38: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    39: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    40: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 2, 'MAX_FEATURES': 'log2'},
    41: {'N_ESTIMATORS': 20, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    42: {'N_ESTIMATORS': 40, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    43: {'N_ESTIMATORS': 100, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    44: {'N_ESTIMATORS': 200, 'CRITERION': 'gini', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    45: {'N_ESTIMATORS': 20, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    46: {'N_ESTIMATORS': 40, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    47: {'N_ESTIMATORS': 100, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
    48: {'N_ESTIMATORS': 200, 'CRITERION': 'entropy', 'MIN_SAMPLES_SPLIT': 8, 'MAX_FEATURES': 'log2'},
}

In [ ]:
for km in parametros_rd.keys():
  parametro_rd = parametros_rd[km]
  resultados_rd.append(execute_classificacao(RandomForestClassifier(n_estimators = parametro_rd['N_ESTIMATORS'],
                                                                    criterion=parametro_rd['CRITERION'], 
                                                                    min_samples_split=parametro_rd['MIN_SAMPLES_SPLIT'],
                                                                    max_features=parametro_rd['MAX_FEATURES']),
                                              X_scaled, 
                                              y))

Classificação: 100%|██████████| 10/10 [00:12<00:00,  1.24s/it]


## **Aplicação do SVM Classifier**

In [ ]:
resultados_svc = []

# Variancia dos Parametros
parametros_svc_1 = {
    1: {'KERNEL': 'linear', 'C': 0.5},
    2: {'KERNEL': 'linear', 'C': 1.0},
    3: {'KERNEL': 'linear', 'C': 2.0}
}

parametros_svc_2 = {
    1: {'KERNEL': 'poly', 'C': 0.5, 'degree': 3, 'gamma': 'scale'},
    2: {'KERNEL': 'poly', 'C': 1.0, 'degree': 3, 'gamma': 'scale'},
    3: {'KERNEL': 'poly', 'C': 2.0, 'degree': 3, 'gamma': 'scale'},
    4: {'KERNEL': 'poly', 'C': 0.5, 'degree': 4, 'gamma': 'scale'},
    5: {'KERNEL': 'poly', 'C': 1.0, 'degree': 4, 'gamma': 'scale'},
    6: {'KERNEL': 'poly', 'C': 2.0, 'degree': 4, 'gamma': 'scale'},
    7: {'KERNEL': 'poly', 'C': 0.5, 'degree': 5, 'gamma': 'scale'},
    8: {'KERNEL': 'poly', 'C': 1.0, 'degree': 5, 'gamma': 'scale'},
    9: {'KERNEL': 'poly', 'C': 2.0, 'degree': 5, 'gamma': 'scale'},
    10: {'KERNEL': 'poly', 'C': 0.5, 'degree': 3, 'gamma': 'auto'},
    11: {'KERNEL': 'poly', 'C': 1.0, 'degree': 3, 'gamma': 'auto'},
    12: {'KERNEL': 'poly', 'C': 2.0, 'degree': 3, 'gamma': 'auto'},
    13: {'KERNEL': 'poly', 'C': 0.5, 'degree': 4, 'gamma': 'auto'},
    14: {'KERNEL': 'poly', 'C': 1.0, 'degree': 4, 'gamma': 'auto'},
    15: {'KERNEL': 'poly', 'C': 2.0, 'degree': 4, 'gamma': 'auto'},
    16: {'KERNEL': 'poly', 'C': 0.5, 'degree': 5, 'gamma': 'auto'},
    17: {'KERNEL': 'poly', 'C': 1.0, 'degree': 5, 'gamma': 'auto'},
    18: {'KERNEL': 'poly', 'C': 2.0, 'degree': 5, 'gamma': 'auto'},
}

parametros_svc_3 = {
    1: {'KERNEL': 'rbf', 'C': 0.5, 'gamma': 'scale'},
    2: {'KERNEL': 'sigmoid', 'C': 0.5, 'gamma': 'scale'},
    3: {'KERNEL': 'rbf', 'C': 1.0, 'gamma': 'scale'},
    4: {'KERNEL': 'sigmoid', 'C': 1.0, 'gamma': 'scale'},
    5: {'KERNEL': 'rbf', 'C': 2.0, 'gamma': 'scale'},
    6: {'KERNEL': 'sigmoid', 'C': 2.0, 'gamma': 'scale'},
    7: {'KERNEL': 'rbf', 'C': 0.5, 'gamma': 'auto'},
    8: {'KERNEL': 'sigmoid', 'C': 0.5, 'gamma': 'auto'},
    9: {'KERNEL': 'rbf', 'C': 1.0, 'gamma': 'auto'},
    10: {'KERNEL': 'sigmoid', 'C': 1.0, 'gamma': 'auto'},
    11: {'KERNEL': 'rbf', 'C': 2.0, 'gamma': 'auto'},
    12: {'KERNEL': 'sigmoid', 'C': 2.0, 'gamma': 'auto'},
}

In [ ]:
for km in parametros_svc_1.keys():
  parametro_svc = parametros_svc_1[km]
  resultados_svc.append(execute_classificacao(SVC(kernel=parametro_svc['KERNEL'],
                                                  C=parametro_svc['C']),
                                               X_scaled, y))

for km in parametros_svc_2.keys():
  parametro_svc_2 = parametros_svc_2[km]
  resultados_svc.append(execute_classificacao(SVC(kernel=parametro_svc_2['KERNEL'],
                                                  C=parametro_svc_2['C'],
                                                  degree=parametro_svc_2['degree'],
                                                  gamma=parametro_svc_2['gamma']),
                                               X_scaled, y))

for km in parametros_svc_3.keys():
  parametro_svc_3 = parametros_svc_3[km]
  resultados_svc.append(execute_classificacao(SVC(kernel=parametro_svc_3['KERNEL'], 
                                                  C=parametro_svc_3['C'],
                                                  gamma=parametro_svc_3['gamma']),
                                               X_scaled, y))

Classificação: 100%|██████████| 10/10 [00:02<00:00,  3.52it/s]


## **Aplicação do KNN Classifier**

In [ ]:
resultados_knn = []

# Variancia dos Parametros
parametros_knn = {
    1: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 2},
    2: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 2},
    3: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 2},
    4: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 2},
    5: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 2},
    6: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 2},
    7: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 2},
    8: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 2},
    9: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 2},
    10: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 2},
    11: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 2},
    12: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 2},
    13: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 2},
    14: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 2},
    15: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 2},
    16: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 2},
    1: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 2},
    2: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 2},
    3: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 2},
    4: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 2},
    5: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 2},
    6: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 2},
    7: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 2},
    8: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 2},
    9: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 2},
    10: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 2},
    11: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 2},
    12: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 2},
    13: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 2},
    14: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 2},
    15: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 2},
    16: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 2},
    17: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 1},
    18: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 1},
    19: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 1},
    20: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 1},
    21: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 1},
    22: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 1},
    23: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 1},
    24: {'N_NEIGHBORS': 3, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 1},
    25: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'uniform', 'P': 1},
    26: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'uniform', 'P': 1},
    27: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'uniform', 'P': 1},
    28: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'uniform', 'P': 1},
    29: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'auto',      'WEIGHTS': 'distance', 'P': 1},
    30: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'ball_tree', 'WEIGHTS': 'distance', 'P': 1},
    31: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'kd_tree',   'WEIGHTS': 'distance', 'P': 1},
    32: {'N_NEIGHBORS': 5, 'METRIC': 'minkowski', 'ALGORITHM': 'brute',     'WEIGHTS': 'distance', 'P': 1},
}

In [ ]:
for km in parametros_knn.keys():
  parametro_knn = parametros_knn[km]
  resultados_knn.append(execute_classificacao(KNeighborsClassifier(n_neighbors=parametro_knn['N_NEIGHBORS'], 
                                                                   metric=parametro_knn['METRIC'], 
                                                                   algorithm=parametro_knn['ALGORITHM'], 
                                                                   weights=parametro_knn['WEIGHTS'], 
                                                                   p=parametro_knn['P']), 
                                              X_scaled, y))

Classificação: 100%|██████████| 10/10 [00:01<00:00,  6.01it/s]


## **Aplicação do MLP Classifier** 

In [ ]:
resultados_mlp = []

# Variancia dos Parametros
parametros_mlp = {
    1: {'MAX_ITER': 1000, 'HIDDEN': (8), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    2: {'MAX_ITER': 1500, 'HIDDEN': (8), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    3: {'MAX_ITER': 1000, 'HIDDEN': (15), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    4: {'MAX_ITER': 1500, 'HIDDEN': (15), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    5: {'MAX_ITER': 1000, 'HIDDEN': (30), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    6: {'MAX_ITER': 1500, 'HIDDEN': (30), 'SOLVER': 'adam', 'ACTIVATION': 'relu'},
    7: {'MAX_ITER': 1000, 'HIDDEN': (8), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    8: {'MAX_ITER': 1500, 'HIDDEN': (8), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    9: {'MAX_ITER': 1000, 'HIDDEN': (15), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    10: {'MAX_ITER': 1500, 'HIDDEN': (15), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    11: {'MAX_ITER': 1000, 'HIDDEN': (30), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    12: {'MAX_ITER': 1500, 'HIDDEN': (30), 'SOLVER': 'sgd', 'ACTIVATION': 'relu'},
    13: {'MAX_ITER': 1000, 'HIDDEN': (8), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    14: {'MAX_ITER': 1500, 'HIDDEN': (8), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    15: {'MAX_ITER': 1000, 'HIDDEN': (15), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    16: {'MAX_ITER': 1500, 'HIDDEN': (15), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    17: {'MAX_ITER': 1000, 'HIDDEN': (30), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    18: {'MAX_ITER': 1500, 'HIDDEN': (30), 'SOLVER': 'adam', 'ACTIVATION': 'logistic'},
    19: {'MAX_ITER': 1000, 'HIDDEN': (8), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'},
    20: {'MAX_ITER': 1500, 'HIDDEN': (8), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'},
    21: {'MAX_ITER': 1000, 'HIDDEN': (15), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'},
    22: {'MAX_ITER': 1500, 'HIDDEN': (15), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'},
    23: {'MAX_ITER': 1000, 'HIDDEN': (30), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'},
    24: {'MAX_ITER': 1500, 'HIDDEN': (30), 'SOLVER': 'sgd', 'ACTIVATION': 'logistic'}
}

In [ ]:
warnings.filterwarnings("ignore")

for km in parametros_mlp.keys():
  parametro_mlp = parametros_mlp[km]
  resultados_mlp.append(execute_classificacao(MLPClassifier(max_iter=parametro_mlp['MAX_ITER'], 
                                                            hidden_layer_sizes=parametro_mlp['HIDDEN'], 
                                                            solver=parametro_mlp['SOLVER'], 
                                                            activation=parametro_mlp['ACTIVATION'],
                                                            verbose=False, 
                                                            tol = 0.00001), 
                                              X_scaled, y))

Classificação: 100%|██████████| 10/10 [01:40<00:00, 10.03s/it]


## **Aplicação do ELM Classifier** 

In [ ]:
resultados_elm = []

# Variancia dos Parametros
parametros_elm = {
    1:  {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'sigmoid',    'C': 1.0, 'RANDOM_TYPE': 'uniform'},
#    2:  {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'relu',       'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    3:  {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'sin',        'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    4:  {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'tanh',       'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    5:  {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'leaky_relu', 'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    6:  {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'sigmoid',    'C': 1.0, 'RANDOM_TYPE': 'uniform'},
#    7:  {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'relu',       'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    8:  {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'sin',        'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    9:  {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'tanh',       'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    10: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'leaky_relu', 'C': 1.0, 'RANDOM_TYPE': 'uniform'},
    11: {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'sigmoid',    'C': 1.0, 'RANDOM_TYPE': 'normal'},
#    12: {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'relu',       'C': 1.0, 'RANDOM_TYPE': 'normal'},
    13: {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'sin',        'C': 1.0, 'RANDOM_TYPE': 'normal'},
    14: {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'tanh',       'C': 1.0, 'RANDOM_TYPE': 'normal'},
    15: {'HIDDEN_UNITS': 60,  'ACTIVATION_FUNCTION': 'leaky_relu', 'C': 1.0, 'RANDOM_TYPE': 'normal'},
    16: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'sigmoid',    'C': 1.0, 'RANDOM_TYPE': 'normal'},
#    17: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'relu',       'C': 1.0, 'RANDOM_TYPE': 'normal'},
    18: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'sin',        'C': 1.0, 'RANDOM_TYPE': 'normal'},
    19: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'tanh',       'C': 1.0, 'RANDOM_TYPE': 'normal'},
    20: {'HIDDEN_UNITS': 100, 'ACTIVATION_FUNCTION': 'leaky_relu', 'C': 1.0, 'RANDOM_TYPE': 'normal'},
}

In [ ]:
for km in parametros_elm.keys():
  parametro_elm = parametros_elm[km]
  resultados_elm.append(execute_classificacaoELM(X_scaled, y, parametro_elm))

Classificação: 100%|██████████| 10/10 [00:00<00:00, 25.44it/s]


#**Etapa 4: Exibição dos Resultados**

## **Definição de funções auxiliares**

**Função que constroe uma tabela com os resultados por rodada**

In [ ]:
# tabela de resultados por rodada
def table_resultados(resultados):

  data_matrix = [['Rodada', 'ACCURACY', 'PRECISION', 'RECALL', 'F1', 'TN (%)', 'FN (%)', 'FP (%)', 'TP (%)', 'TN', 'FN', 'FP', 'TP']]

  for rodada in range(MAX_RODADAS):
    accuracy = resultados['ACCURACY'][rodada]
    precision = resultados['PRECISION'][rodada]
    recall = resultados['RECALL'][rodada]
    f1 = resultados['F1'][rodada]

    tnp = resultados['TN (%)'][rodada]
    fnp = resultados['FN (%)'][rodada]
    fpp = resultados['FP (%)'][rodada]
    tpp = resultados['TP (%)'][rodada]
    
    tn = resultados['TN'][rodada]
    fn = resultados['FN'][rodada]
    fp = resultados['FP'][rodada]
    tp = resultados['TP'][rodada]

    score = [
      rodada + 1,
      round(accuracy,3),
      round(precision,3),
      round(recall,3),
      round(f1,3),
      round(tnp, 3),
      round(fnp, 3),
      round(fpp, 3),
      round(tpp, 3),
      round(tn, 3),
      round(fn, 3),
      round(fp, 3),
      round(tp, 3),
    ]

    data_matrix.append(score)

  fig = ff.create_table(data_matrix, height_constant=20)
  fig.show()
  print('\n')

## **Resultados por rodada**

**Resultados de Random Forest Classifier**

In [ ]:
for i in range(len(resultados_rd)):
  table_resultados(resultados_rd[i])

**Resultados de SVM Classifier**

In [ ]:
for i in range(len(resultados_svc)):
  table_resultados(resultados_svc[i])

**Resultados de KNN Classifier**

In [ ]:
for i in range(len(resultados_knn)):
  table_resultados(resultados_knn[i])

**Resultados de MLP Classifier**

In [ ]:
for i in range(len(resultados_mlp)):
  table_resultados(resultados_mlp[i])

**Resultados de ELM Classifier**

In [ ]:
for i in range(len(resultados_elm)):
  table_resultados(resultados_elm[i])

**Função que constroe uma tabela com os resultados por modelo de Classificação**

In [ ]:
# tabela de resultados por modelo de regressão
def table_comparacao(resultados):

  data_matrix = [['Rodada', 'ACCURACY', 'PRECISION', 'RECALL', 'F1', 'TN (%)', 'FN (%)', 'FP (%)', 'TP (%)', 'TN', 'FN', 'FP', 'TP']]

  for tecnica in resultados.keys():

    media_accuracy = resultados[tecnica]['ACCURACY']
    media_precision = resultados[tecnica]['PRECISION']
    media_recall = resultados[tecnica]['RECALL']
    media_f1 = resultados[tecnica]['F1']

    media_tnp = resultados[tecnica]['TN (%)']
    media_fnp = resultados[tecnica]['FN (%)']
    media_fpp = resultados[tecnica]['FP (%)']
    media_tpp = resultados[tecnica]['TP (%)']
    
    media_tn = resultados[tecnica]['TN']
    media_fn = resultados[tecnica]['FN']
    media_fp = resultados[tecnica]['FP']
    media_tp = resultados[tecnica]['TP']

    score = [
      tecnica,
      round(media_accuracy,3),
      round(media_precision,3),
      round(media_recall,3),
      round(media_f1,3),
      round(media_tnp, 3),
      round(media_fnp, 3),
      round(media_fpp, 3),
      round(media_tpp, 3),
      round(media_tn, 3),
      round(media_fn, 3),
      round(media_fp, 3),
      round(media_tp, 3)
    ]

    data_matrix.append(score)

  fig = ff.create_table(data_matrix, height_constant=20)
  fig.show()

**Função que calcula as médias de cada métrica**

In [ ]:
def calcula_media_scores(resultados):
  medias = {}
  medias['ACCURACY'] = np.mean(resultados['ACCURACY'])
  medias['PRECISION'] = np.mean(resultados['PRECISION'])
  medias['RECALL'] = np.mean(resultados['RECALL'])
  medias['F1'] = np.mean(resultados['F1'])
  medias['TN (%)'] = np.mean(resultados['TN (%)'])
  medias['FN (%)'] = np.mean(resultados['FN (%)'])
  medias['FP (%)'] = np.mean(resultados['FP (%)'])
  medias['TP (%)'] = np.mean(resultados['TP (%)'])
  
  medias['TN'] = np.mean(resultados['TN'])
  medias['FN'] = np.mean(resultados['FN'])
  medias['FP'] = np.mean(resultados['FP'])
  medias['TP'] = np.mean(resultados['TP'])

  return medias

## **Análise comparativa**

In [ ]:
# Armazena o resultado médio de cada métrica
resultado_final= {}

In [ ]:
# Calcula a média das métricas de Random Forest Classifier
for i in range(len(resultados_rd)):
  resultado_final['RF ('+str(i+1)+')'] = calcula_media_scores(resultados_rd[i])
 
# Calcula a média das métricas de SVM Classifier
for i in range(len(resultados_svc)):
  resultado_final['SVC ('+str(i+1)+')'] = calcula_media_scores(resultados_svc[i])

# Calcula a média das métricas de KNN Classifier
for i in range(len(resultados_knn)):
  resultado_final['KNN ('+str(i+1)+')'] = calcula_media_scores(resultados_knn[i])

# Calcula a média das métricas de MLP Classifier
for i in range(len(resultados_mlp)):
  resultado_final['MLP ('+str(i+1)+')'] = calcula_media_scores(resultados_mlp[i])

In [ ]:
# Calcula a média das métricas de MLP Classifier
for i in range(len(resultados_elm)):
  resultado_final['ELM ('+str(i+1)+')'] = calcula_media_scores(resultados_elm[i])

In [ ]:
table_comparacao(resultado_final)